In [1]:
import sys
from importlib import reload
reload(sys)
#sys.setdefaultencoding('utf-8')

import TD_RvNN_exp
import math

import theano
from theano import tensor as T
import numpy as np
from numpy.testing import assert_array_almost_equal

import time
import datetime
import random
from evaluate import *

In [2]:
trainPath = "../resource/rumoureval-2019-training-data.zip"
testPath = "../resource/rumoureval-2019-test-data.zip"

In [3]:
testLabelPath = "../resource/final-eval-key.json" # evaluation file contains test labels

In [4]:
import TD_RvNN

In [5]:
# load data => find the labels for training and test data and put them into a dict structured as needed in RvNN approach
# at first handle zip files
from zipfile import ZipFile
from typing import Dict
def get_archive_directory_structure(archive: ZipFile) -> Dict:
    result = {}
    for file in archive.namelist():
        # Skip directories in archive.
        if file.endswith('/'):
            continue

        d = result
        path = file.split('/')[1:]  # [1:] to skip top-level directory.
        for p in path[:-1]:  # [:-1] to skip filename
            if p not in d:
                d[p] = {}
            d = d[p]
        d[path[-1]] = file
    return result

In [6]:
training_data_archive = ZipFile(trainPath)
training_data_contents = get_archive_directory_structure(
        training_data_archive)

In [7]:
training_data_contents

{'dev-key.json': 'rumoureval-2019-training-data/dev-key.json',
 'reddit-dev-data': {'1jvbd8': {'raw.json': 'rumoureval-2019-training-data/reddit-dev-data/1jvbd8/raw.json',
   'replies': {'cbiol38.json': 'rumoureval-2019-training-data/reddit-dev-data/1jvbd8/replies/cbiol38.json',
    'cbiwlli.json': 'rumoureval-2019-training-data/reddit-dev-data/1jvbd8/replies/cbiwlli.json',
    'cbj4pcw.json': 'rumoureval-2019-training-data/reddit-dev-data/1jvbd8/replies/cbj4pcw.json',
    'cbkixew.json': 'rumoureval-2019-training-data/reddit-dev-data/1jvbd8/replies/cbkixew.json'},
   'source-tweet': {'1jvbd8.json': 'rumoureval-2019-training-data/reddit-dev-data/1jvbd8/source-tweet/1jvbd8.json'},
   'structure.json': 'rumoureval-2019-training-data/reddit-dev-data/1jvbd8/structure.json'},
  '31xv6u': {'raw.json': 'rumoureval-2019-training-data/reddit-dev-data/31xv6u/raw.json',
   'replies': {'cq64vk3.json': 'rumoureval-2019-training-data/reddit-dev-data/31xv6u/replies/cq64vk3.json',
    'cq674h2.json': 

In [8]:
import json

In [9]:
train_labels = json.loads(training_data_archive.read(training_data_contents['train-key.json']))
train_labels

{'subtaskaenglish': {'501760642928635904': 'comment',
  '500270212198174720': 'comment',
  '524971210275565568': 'comment',
  '552836882770690049': 'comment',
  '500289931097296897': 'support',
  '544293230649810944': 'comment',
  '544283032732332032': 'comment',
  '500406679176241153': 'comment',
  '500300182844878848': 'comment',
  '552811591683821568': 'comment',
  '524938343180931073': 'comment',
  '521360786409943041': 'deny',
  '524946532416884736': 'comment',
  '544347456238931968': 'comment',
  '525020658972258305': 'query',
  '552817834628501505': 'comment',
  '524959078229880832': 'comment',
  '553588165408473088': 'comment',
  '544293748377518080': 'comment',
  '553196346375954433': 'query',
  '524957146656821249': 'comment',
  '524992668301262848': 'deny',
  '500294827351621632': 'comment',
  '544307827070615553': 'support',
  '524955418955902976': 'comment',
  '553541495588802560': 'comment',
  '500301494193627136': 'comment',
  '525026551411519488': 'comment',
  '55356514

In [10]:
dev_labels = json.loads(training_data_archive.read(training_data_contents['dev-key.json']))

In [11]:
test_labels = json.load(open(testLabelPath,'r'))
test_labels

{'subtaskaenglish': {'443938194715713536': 'support',
  '774165935041093633': 'support',
  '784071228248109057': 'support',
  '784118929799073793': 'support',
  '784216706080178176': 'support',
  '784316107645603840': 'support',
  '828933929080086528': 'support',
  '830469481621241857': 'support',
  '852844529778601985': 'support',
  '872300483272114177': 'support',
  '872367878871408640': 'support',
  '892781499103277056': 'support',
  '897502435593265152': 'query',
  '897715873145913344': 'support',
  '901939374375370752': 'support',
  '902006921523331073': 'support',
  '902134516575346688': 'support',
  '902224586967621633': 'support',
  '902542822540173314': 'support',
  '902595384635043840': 'support',
  '903336023362547715': 'query',
  '903528113631584256': 'support',
  '904111594912841729': 'support',
  '904200288059494400': 'support',
  '904725019372253184': 'support',
  '904727149747326977': 'support',
  '904762977185808385': 'support',
  '905161219274940416': 'support',
  '90

In [12]:
len(train_labels['subtaskbenglish'])

327

In [13]:
labelDic, indexDic = {}, {} # labelDic contains all (eid,label) connections and indexDic contains (idx, eid) translation
eid = 1 # start indexing at one and assign each new tweet an index eid+=1        # to make indexing more simple and avoid
for (idx, label) in train_labels['subtaskbenglish'].items():                            # 18 digit numbers
    if len(idx) == 18: # at first only consider the twitter IDs and labels
        indexDic[idx] = eid # keep connection between simple index and 18 digit index for look-ups later
        labelDic[eid] = label.lower()
        eid += 1 # increase index by one for the next tweet

In [14]:
indexDic

{'500288349924782080': 1,
 '500308076004929537': 2,
 '544282227035869184': 3,
 '529695367680761856': 4,
 '544324444773433348': 5,
 '544350712365207552': 6,
 '500389488217309184': 7,
 '552806309540528128': 8,
 '552978099357237248': 9,
 '524956129017995264': 10,
 '500332933098385408': 11,
 '544271362022338560': 12,
 '544514564407427072': 13,
 '553587672137334785': 14,
 '500363126294863876': 15,
 '553474188259102720': 16,
 '500394061887709184': 17,
 '544309275141885952': 18,
 '552811386259386370': 19,
 '524925987239120897': 20,
 '576323086888361984': 21,
 '544314234541469696': 22,
 '544381485591982083': 23,
 '553505242554175489': 24,
 '544278985249550337': 25,
 '553586897168392192': 26,
 '524975705206304769': 27,
 '529653029747064832': 28,
 '577258317942149120': 29,
 '544367462012432384': 30,
 '529654186791944192': 31,
 '552792913910833152': 32,
 '524923462398513152': 33,
 '524952883343925249': 34,
 '544491151118860289': 35,
 '544515538383564801': 36,
 '524925050739490816': 37,
 '50028042

In [15]:
for (idx, label) in dev_labels['subtaskbenglish'].items():
    if len(idx) == 18: # at first only consider the twitter IDs and labels
        indexDic[idx] = eid
        labelDic[eid] = label.lower()
        eid += 1

In [16]:
len(labelDic)

325

In [17]:
for (idx, label) in test_labels['subtaskbenglish'].items():
    if len(idx) == 18: # at first only consider the twitter IDs and labels
        indexDic[idx] = eid
        labelDic[eid] = label.lower()
        eid += 1

In [18]:
highest_source_eid = eid # keep this value to continue counting upwards for simpler reply indices later
len(labelDic)

381

In [19]:
labelDic # contains ALL labels for training, dev and test dataset

{1: 'unverified',
 2: 'unverified',
 3: 'true',
 4: 'false',
 5: 'true',
 6: 'true',
 7: 'unverified',
 8: 'false',
 9: 'false',
 10: 'false',
 11: 'unverified',
 12: 'true',
 13: 'true',
 14: 'true',
 15: 'unverified',
 16: 'unverified',
 17: 'unverified',
 18: 'false',
 19: 'true',
 20: 'true',
 21: 'unverified',
 22: 'true',
 23: 'true',
 24: 'unverified',
 25: 'true',
 26: 'true',
 27: 'true',
 28: 'false',
 29: 'unverified',
 30: 'true',
 31: 'false',
 32: 'true',
 33: 'true',
 34: 'true',
 35: 'true',
 36: 'true',
 37: 'true',
 38: 'unverified',
 39: 'false',
 40: 'unverified',
 41: 'unverified',
 42: 'false',
 43: 'false',
 44: 'unverified',
 45: 'unverified',
 46: 'unverified',
 47: 'true',
 48: 'true',
 49: 'true',
 50: 'true',
 51: 'true',
 52: 'true',
 53: 'false',
 54: 'false',
 55: 'false',
 56: 'unverified',
 57: 'true',
 58: 'unverified',
 59: 'unverified',
 60: 'unverified',
 61: 'unverified',
 62: 'false',
 63: 'true',
 64: 'unverified',
 65: 'true',
 66: 'unverified',

In [20]:
# generating the tree from all the zipped data
twitter_english = training_data_contents['twitter-english']

In [21]:
test_data_archive = ZipFile(testPath)
test_data_contents = get_archive_directory_structure(test_data_archive)
twitter_en_test_data = test_data_contents['twitter-en-test-data']

In [22]:
# calculate parent_num, indexP and indexC for the treeDic
def calc_parent_num(tree_branch: Dict) -> int: # go recursively through tree and calculate parent_num
    if isinstance(tree_branch, Dict):
        return 1 + (max(map(calc_parent_num, tree_branch.values())) if tree_branch else 0)
    return 0

In [23]:
def find_parent_node(tree_branch: Dict, reply_idx: int): # go recursively through the tree and find parent index
    for indexP, sub_branch in tree_branch.items(): # keep indexP and go through the keys
        if reply_idx in sub_branch: # search for indexC in the keys
            return indexP # if it is found, return the parent node
        elif isinstance(sub_branch, dict): # else check if the keys itself are a dictionary
            parent_node = find_parent_node(sub_branch, reply_idx) # if so, recursively call again the function with the subtree 
            if parent_node is not None: # return the value only if it exists (otherwise we should add try and catch later)
                return parent_node

In [24]:
indexDic

{'500288349924782080': 1,
 '500308076004929537': 2,
 '544282227035869184': 3,
 '529695367680761856': 4,
 '544324444773433348': 5,
 '544350712365207552': 6,
 '500389488217309184': 7,
 '552806309540528128': 8,
 '552978099357237248': 9,
 '524956129017995264': 10,
 '500332933098385408': 11,
 '544271362022338560': 12,
 '544514564407427072': 13,
 '553587672137334785': 14,
 '500363126294863876': 15,
 '553474188259102720': 16,
 '500394061887709184': 17,
 '544309275141885952': 18,
 '552811386259386370': 19,
 '524925987239120897': 20,
 '576323086888361984': 21,
 '544314234541469696': 22,
 '544381485591982083': 23,
 '553505242554175489': 24,
 '544278985249550337': 25,
 '553586897168392192': 26,
 '524975705206304769': 27,
 '529653029747064832': 28,
 '577258317942149120': 29,
 '544367462012432384': 30,
 '529654186791944192': 31,
 '552792913910833152': 32,
 '524923462398513152': 33,
 '524952883343925249': 34,
 '544491151118860289': 35,
 '544515538383564801': 36,
 '524925050739490816': 37,
 '50028042

In [25]:
# create treeDic
treeDic = {}
word_index = 0 # give every word a unique index starting with 0
words = {} # dict containing words of all posts combined => ('word':word_index)
for archive, topics in [(training_data_archive, twitter_english.items()),
                            (test_data_archive, twitter_en_test_data.items())]:
    for topic, threads in topics:
        for thread in threads.values():
            maxL = 0 # maximum post length of each thread => reset to 0 for each new thread
            # get the source information as a Dict (contains all info about the source post)
            source_information = json.loads(archive.read(list(thread['source-tweet'].values())[0]))
            idx = source_information['id'] # get the 18 digit source ID
            eid = indexDic[str(idx)] # convert it to the corresponding simpler ID
            post_structure = json.loads(archive.read(thread['structure.json'])) # get the thread structure as a Dict
            parent_num = calc_parent_num(post_structure) # calculate the number of reply levels in each thread structure
            #print(eid, parent_num,  " PAUSE ")
            indexC = eid # initialize post index with source post index
            
            text_information = source_information['text']
            Vec = str() # every new iteration empty the string containing word_index:word_frequency pairs
            words_per_post = {} # dict with frequencies for every word in a post; reset for every post
            count_post_length = 0 # reset for every loop iteration
            for word in text_information.split(): # iterate through words of post
                if word not in words.keys() and not word.startswith('http'):
                    words[word] = word_index # give every word a unique index
                    word_index += 1
                elif 'URL' not in words.keys() and word.startswith('http'):
                    words['URL'] = word_index # save every URL as one word with the same index
                    word_index += 1
                count_post_length += 1

                if word not in words_per_post.keys() and not word.startswith('http'):
                    words_per_post[word] = 1
                elif 'URL' not in words_per_post.keys() and word.startswith('http'):
                    words_per_post['URL'] = 1
                elif word in words_per_post.keys() and not word.startswith('http'):
                    words_per_post[word] += 1
                else:
                    words_per_post['URL'] += 1

            iteration = 0 # count iterations to get the last iteration and not put ' ' at the end of Vec
            for word in words_per_post.keys(): # iterate through words of post a second time to get the right numbers
                if word.startswith('http'):
                    Vec += str(words['URL']) + ':' + str(words_per_post['URL'])
                else:
                    Vec += str(words[word]) + ':' + str(words_per_post[word])
                iteration += 1
                if iteration != len(words_per_post.keys()): # if it's not the end of the tweet
                    Vec += ' ' # add space between the word index/frequency pairs

            if maxL < count_post_length: # new maximum post length found
                maxL = count_post_length
                
            if idx not in treeDic: # create empty entry first to make the key accessable
                treeDic[idx] = {}
            treeDic[idx][indexC] = {'parent':'None', 'parent_num':parent_num, 'maxL':0, 'vec':Vec}
            if 'replies' in thread: # some "replies" folders seem to be empty and then this for loop would throw an error
                for reply in thread['replies'].values(): # for every reply post
                    # get the reply information as a Dict (contains all info about the reply post)
                    reply_information = json.loads(archive.read(reply))
                    reply_idx = reply_information['id']
                    indexC = highest_source_eid # convert 18 digit index to simpler index
                    indexDic[str(reply_idx)] = highest_source_eid # save connection between IDs (18 digit and simple)
                    # find out parent of each reply node
                    indexP = find_parent_node(post_structure, str(reply_idx))
                    
                    text_information = reply_information['text']
                    #print(text_information)
                    Vec = str() # every new iteration empty the string containing word_index:word_frequency pairs
                    words_per_post = {} # dict with frequencies for every word in a post; reset for every post
                    count_post_length = 0 # reset for every loop iteration
                    for word in text_information.split(): # iterate through words of post
                        if word not in words.keys() and not word.startswith('http'):
                            words[word] = word_index # give every word a unique index
                            word_index += 1
                        elif 'URL' not in words.keys() and word.startswith('http'):
                            words['URL'] = word_index # save every URL as one word with the same index
                            word_index += 1
                        count_post_length += 1

                        if word not in words_per_post.keys() and not word.startswith('http'):
                            words_per_post[word] = 1
                        elif 'URL' not in words_per_post.keys() and word.startswith('http'):
                            words_per_post['URL'] = 1
                        elif word in words_per_post.keys() and not word.startswith('http'):
                            words_per_post[word] += 1
                        else:
                            words_per_post['URL'] += 1

                    iteration = 0 # count iterations to get the last iteration and not put ' ' at the end of Vec
                    for word in words_per_post.keys(): # iterate through words of post a second time to get the right numbers
                        if word.startswith('http'):
                            Vec += str(words['URL']) + ':' + str(words_per_post['URL'])
                        else:
                            Vec += str(words[word]) + ':' + str(words_per_post[word])
                        iteration += 1
                        if iteration != len(words_per_post.keys()): # if it's not the end of the tweet
                            Vec += ' ' # add space between the word index/frequency pairs

                    if maxL < count_post_length: # new maximum post length found
                        maxL = count_post_length
                        maxIdx = idx
                        maxIndexC = indexC
                    
                    #print(indexC, indexP, parent_num, indexP in indexDic)
                    treeDic[idx][indexC] = {'parent':indexP, 'parent_num':parent_num, 'maxL':0, 'vec':Vec}
                    highest_source_eid += 1 # increase index for the next reply
                    
            for post in treeDic[idx].values(): # go through all posts again to set the maxL for every thread
                post['maxL'] = maxL
            #print(treeDic[idx])        
        #for thread in thread.values(): # iterate through thread another time to add missing parameters to tree
            # todo: add the right values to the tree

In [26]:
treeDic

{552783667052167168: {91: {'parent': 'None',
   'parent_num': 4,
   'maxL': 22,
   'vec': '0:1 1:1 2:1 3:1 4:1 5:1 6:1 7:1 8:1 9:1 10:1 11:1 12:1 13:1 14:1 15:1 16:1'},
  382: {'parent': '552783667052167168',
   'parent_num': 4,
   'maxL': 22,
   'vec': '17:1 18:1 0:1 1:1 3:1 4:1 5:1 6:1 7:1 8:1 9:1 10:1 19:1 20:1 21:1 22:1 23:1 24:1 25:1 26:1 27:1'},
  383: {'parent': '552785374507175936',
   'parent_num': 4,
   'maxL': 22,
   'vec': '28:1 29:1 30:1 31:1 32:1 33:1 34:1 35:1 23:1 36:1 37:1 38:1 39:1 14:1 40:1 41:1'},
  384: {'parent': '552786226546495488',
   'parent_num': 4,
   'maxL': 22,
   'vec': '42:1 43:1 44:1 45:1 46:1 47:1 48:1 49:1'},
  385: {'parent': '552783667052167168',
   'parent_num': 4,
   'maxL': 22,
   'vec': '18:1 50:1 51:1 52:1 53:1 8:1 54:1 55:1 56:1 57:1 58:1 59:1'},
  386: {'parent': '552783667052167168',
   'parent_num': 4,
   'maxL': 22,
   'vec': '18:1 60:1 61:1 62:1 63:1 64:1 65:1 66:1 67:1 68:1 69:1 70:1 71:1 72:1 32:1 73:1 74:1 75:1 76:1 77:1 78:1 79:1'}},


In [27]:
# iterate through treeDic again and change parent indices to the corresponding smaller values of indexDic
# and also delete tree branches that contain posts which don't appear in the dataset
for i,v in treeDic.items():
    for j,w in list(v.items()):
        if not w['parent'] == 'None':
            if w['parent'] in indexDic:
                #print(w['parent'], " before")
                w['parent'] = indexDic[w['parent']]
                #print(w['parent'], " after")
            else: # delete all branches in the tree which start with IDs that don't appear in the actual data 
                print(w['parent'], w) # (because there is no statistical significance if we can't track the posts
                print("whole branch ", treeDic[i][j])   # they refer to)
                del treeDic[i][j]

553485679129534464 {'parent': '553485679129534464', 'parent_num': 4, 'maxL': 22, 'vec': '2915:1 2916:1 405:1 2691:1 151:1 69:1 1387:1 378:1 2917:1 14:1 25:1 2918:1 2523:1 438:1 312:1 343:1 40:1 2919:1 2920:1'}
whole branch  {'parent': '553485679129534464', 'parent_num': 4, 'maxL': 22, 'vec': '2915:1 2916:1 405:1 2691:1 151:1 69:1 1387:1 378:1 2917:1 14:1 25:1 2918:1 2523:1 438:1 312:1 343:1 40:1 2919:1 2920:1'}
553490097623269376 {'parent': '553490097623269376', 'parent_num': 4, 'maxL': 22, 'vec': '2915:1 2916:1 405:1 2691:1 94:1 1254:1 150:1 1924:1 64:1 23:1 2921:1 1474:1 1977:1 377:1 285:1 349:1 1111:1'}
whole branch  {'parent': '553490097623269376', 'parent_num': 4, 'maxL': 22, 'vec': '2915:1 2916:1 405:1 2691:1 94:1 1254:1 150:1 1924:1 64:1 23:1 2921:1 1474:1 1977:1 377:1 285:1 349:1 1111:1'}


In [28]:
treeDic

{552783667052167168: {91: {'parent': 'None',
   'parent_num': 4,
   'maxL': 22,
   'vec': '0:1 1:1 2:1 3:1 4:1 5:1 6:1 7:1 8:1 9:1 10:1 11:1 12:1 13:1 14:1 15:1 16:1'},
  382: {'parent': 91,
   'parent_num': 4,
   'maxL': 22,
   'vec': '17:1 18:1 0:1 1:1 3:1 4:1 5:1 6:1 7:1 8:1 9:1 10:1 19:1 20:1 21:1 22:1 23:1 24:1 25:1 26:1 27:1'},
  383: {'parent': 382,
   'parent_num': 4,
   'maxL': 22,
   'vec': '28:1 29:1 30:1 31:1 32:1 33:1 34:1 35:1 23:1 36:1 37:1 38:1 39:1 14:1 40:1 41:1'},
  384: {'parent': 383,
   'parent_num': 4,
   'maxL': 22,
   'vec': '42:1 43:1 44:1 45:1 46:1 47:1 48:1 49:1'},
  385: {'parent': 91,
   'parent_num': 4,
   'maxL': 22,
   'vec': '18:1 50:1 51:1 52:1 53:1 8:1 54:1 55:1 56:1 57:1 58:1 59:1'},
  386: {'parent': 91,
   'parent_num': 4,
   'maxL': 22,
   'vec': '18:1 60:1 61:1 62:1 63:1 64:1 65:1 66:1 67:1 68:1 69:1 70:1 71:1 72:1 32:1 73:1 74:1 75:1 76:1 77:1 78:1 79:1'}},
 552785375161499649: {72: {'parent': 'None',
   'parent_num': 2,
   'maxL': 18,
   'vec'

In [29]:
labelDic

{1: 'unverified',
 2: 'unverified',
 3: 'true',
 4: 'false',
 5: 'true',
 6: 'true',
 7: 'unverified',
 8: 'false',
 9: 'false',
 10: 'false',
 11: 'unverified',
 12: 'true',
 13: 'true',
 14: 'true',
 15: 'unverified',
 16: 'unverified',
 17: 'unverified',
 18: 'false',
 19: 'true',
 20: 'true',
 21: 'unverified',
 22: 'true',
 23: 'true',
 24: 'unverified',
 25: 'true',
 26: 'true',
 27: 'true',
 28: 'false',
 29: 'unverified',
 30: 'true',
 31: 'false',
 32: 'true',
 33: 'true',
 34: 'true',
 35: 'true',
 36: 'true',
 37: 'true',
 38: 'unverified',
 39: 'false',
 40: 'unverified',
 41: 'unverified',
 42: 'false',
 43: 'false',
 44: 'unverified',
 45: 'unverified',
 46: 'unverified',
 47: 'true',
 48: 'true',
 49: 'true',
 50: 'true',
 51: 'true',
 52: 'true',
 53: 'false',
 54: 'false',
 55: 'false',
 56: 'unverified',
 57: 'true',
 58: 'unverified',
 59: 'unverified',
 60: 'unverified',
 61: 'unverified',
 62: 'false',
 63: 'true',
 64: 'unverified',
 65: 'true',
 66: 'unverified',

In [30]:
def str2matrix(Str, MaxL): # str = index:wordfreq index:wordfreq
    wordFreq, wordIndex = [], []
    l = 0
    for pair in Str.split(' '):
        wordFreq.append(float(pair.split(':')[1]))
        wordIndex.append(int(pair.split(':')[0]))
        l += 1
    ladd = [ 0 for i in range( MaxL-l ) ]
    wordFreq += ladd 
    wordIndex += ladd 
    #print MaxL, l, len(Str.split(' ')), len(wordFreq)
    #print Str.split(' ')
    return wordFreq, wordIndex

In [31]:
train_IDs, test_IDs = [], []

In [32]:
for (eid, label) in train_labels['subtaskbenglish'].items():
    if len(eid) == 18: # for now only consider the twitter IDs and labels
        train_IDs.append(eid)
for (eid, label) in dev_labels['subtaskbenglish'].items():
    if len(eid) == 18: # for now only consider the twitter IDs and labels
        train_IDs.append(eid)
for (eid, label) in test_labels['subtaskbenglish'].items():
    if len(eid) == 18: # for now only consider the twitter IDs and labels
        test_IDs.append(eid)

In [33]:
# load label function
def loadLabel(label, l1, l2, l3):
    labelset_f, labelset_t, labelset_u = ['false'], ['true'], ['unverified']
    if label in labelset_f:
       y_train = [1,0,0]
       l1 += 1
    if label in labelset_t:
       y_train = [0,1,0]
       l2 += 1
    if label in labelset_u:
       y_train = [0,0,1]
       l3 += 1
    return y_train, l1,l2,l3

In [34]:
def constructTree(tree):
    ## tree: {index1:{'parent':, 'maxL':, 'vec':}
    ## 1. ini tree node
    index2node = {}
    for i in tree:
        node = TD_RvNN_exp.Node_tweet(idx=i)
        index2node[i] = node
    ## 2. construct tree
    for j in tree:
        indexC = j
        indexP = tree[j]['parent']
        nodeC = index2node[indexC]
        wordFreq, wordIndex = str2matrix( tree[j]['vec'], tree[j]['maxL'] )
        #print tree[j]['maxL']
        nodeC.index = wordIndex
        nodeC.word = wordFreq
        #nodeC.time = tree[j]['post_t']
        ## not root node ## 
        if not indexP == 'None':
            if int(indexP) in index2node: # there are two IDs listed in the structure files which don't exist in the training set
                nodeP = index2node[int(indexP)]       # => filter them out
                nodeC.parent = nodeP
                nodeP.children.append(nodeC)
        ## root node ##
        else:
            root = nodeC
    ## 3. convert tree to DNN input    
    parent_num = tree[j]['parent_num'] 
    ini_x, ini_index = str2matrix( "0:0", tree[j]['maxL'] )
    x_word, x_index, tree = TD_RvNN.gen_nn_inputs(root, ini_x) # put root node (with all children) and 0 array with maxL
    return x_word, x_index, tree, parent_num

In [35]:
tree_train, word_train, index_train, y_train, parent_num_train, c = [], [], [], [], [], 0
l1,l2,l3 = 0,0,0
for eid in train_IDs:
    print(eid)
    if indexDic[eid] not in labelDic: continue
    if int(eid) not in treeDic: continue
    if len(treeDic[int(eid)]) <= 0:
        continue
    label = labelDic[indexDic[eid]]
    y, l1,l2,l3 = loadLabel(label, l1, l2, l3)
    y_train.append(y)
    x_word, x_index, tree, parent_num = constructTree(treeDic[int(eid)])
    tree_train.append(tree)
    word_train.append(x_word)
    index_train.append(x_index)
    parent_num_train.append(parent_num)
    c += 1
    print(tree)
print(l1, l2, l3)

500288349924782080
[[   0    1]
 [   1 1999]
 [   1 2000]
 [   1 2001]
 [   1 2002]
 [   1 2003]
 [   1 2005]
 [   1 2006]
 [   1 2010]
 [   1 2011]
 [2002 2004]
 [2005 2007]
 [2007 2008]
 [2008 2009]]
500308076004929537
[[   0    2]
 [   2 2236]
 [   2 2238]
 [   2 2239]
 [   2 2240]
 [   2 2244]
 [   2 2245]
 [   2 2246]
 [   2 2250]
 [2236 2237]
 [2238 2248]
 [2238 2251]
 [2239 2242]
 [2239 2243]
 [2250 2252]
 [2237 2241]
 [2243 2247]
 [2243 2249]
 [2243 2253]]
544282227035869184
[[   0    3]
 [   3 4723]
 [   3 4724]
 [   3 4725]
 [   3 4726]
 [   3 4727]
 [   3 4728]
 [   3 4729]
 [   3 4730]
 [   3 4731]
 [   3 4732]
 [   3 4733]
 [   3 4734]]
529695367680761856
[[   0    4]
 [   4 4405]
 [   4 4406]
 [   4 4407]
 [   4 4408]
 [   4 4409]
 [   4 4412]
 [4409 4410]
 [4410 4411]]
544324444773433348
[[   0    5]
 [   5 5097]
 [   5 5098]
 [   5 5099]
 [   5 5100]
 [   5 5101]
 [   5 5102]
 [   5 5103]
 [   5 5104]
 [   5 5105]
 [   5 5106]
 [   5 5107]
 [   5 5108]
 [   5 5109]
 [  

 [ 232 5544]]
525049639016615937
[[   0  233]
 [ 233 4313]
 [ 233 4314]
 [ 233 4315]
 [ 233 4316]
 [ 233 4317]]
553478289474740224
[[  0 234]
 [234 935]
 [234 937]
 [234 938]
 [234 939]
 [234 940]
 [935 936]]
500281131057811456
[[   0  235]
 [ 235 1906]
 [ 235 1907]
 [ 235 1908]
 [ 235 1909]
 [ 235 1910]
 [ 235 1911]
 [ 235 1912]
 [ 235 1913]
 [ 235 1914]
 [ 235 1916]
 [ 235 1917]
 [ 235 1918]
 [ 235 1919]
 [ 235 1920]
 [ 235 1921]
 [1912 1915]
 [1912 1922]
 [1922 1923]
 [1923 1924]
 [1924 1925]]
553538058440941568
[[   0  236]
 [ 236 1102]
 [ 236 1103]
 [ 236 1104]
 [ 236 1105]
 [ 236 1106]
 [ 236 1107]
 [ 236 1108]
 [ 236 1109]
 [ 236 1110]
 [ 236 1111]
 [ 236 1112]
 [ 236 1113]
 [ 236 1114]
 [ 236 1116]
 [ 236 1118]
 [ 236 1119]
 [ 236 1120]
 [1113 1115]
 [1113 1117]]
524926472432410625
[[   0  237]
 [ 237 3668]
 [ 237 3669]
 [ 237 3670]]
525023025792835585
[[   0  238]
 [ 238 4265]
 [ 238 4266]
 [ 238 4267]
 [ 238 4268]
 [ 238 4269]
 [ 238 4270]
 [ 238 4271]
 [ 238 4272]
 [ 238 427

In [36]:
x_word

array([[1., 1., 1., 2., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 0.,
        0., 0., 0., 0., 0., 0., 0., 0.],
       [1., 1., 1., 1., 1., 1., 1., 2., 1., 1., 1., 1., 1., 1., 1., 1.,
        0., 0., 0., 0., 0., 0., 0., 0.],
       [1., 1., 1., 1., 1., 1., 1., 1., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0.],
       [1., 1., 2., 1., 1., 1., 1., 1., 1., 2., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 0., 0.],
       [1., 1., 1., 1., 1., 1., 2., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        0., 0., 0., 0., 0., 0., 0., 0.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0.],
       [4., 4., 3., 1., 1., 1., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 

In [37]:
print("loading test set",)
tree_test, word_test, index_test, parent_num_test, y_test, c = [], [], [], [], [], 0
l1,l2,l3 = 0,0,0
for eid in test_IDs:
    print(eid)
    if indexDic[eid] not in labelDic: 
        print("1")
        continue
    if int(eid) not in treeDic:
        print("2")
        continue
    if len(treeDic[int(eid)]) <= 0:
        print("3")
        continue    
    label = labelDic[indexDic[eid]]
    y, l1,l2,l3 = loadLabel(label, l1, l2, l3)
    y_test.append(y)
    ## 2. construct tree
    x_word, x_index, tree, parent_num = constructTree(treeDic[int(eid)])
    tree_test.append(tree)
    word_test.append(x_word)
    index_test.append(x_index)
    parent_num_test.append(parent_num)
    c += 1
    print(tree)
print(l1,l2,l3)
print("train no:", len(tree_train), len(parent_num_train), len(y_train))
print("test no:", len(tree_test), len(parent_num_test), len(y_test))
print("dim1 for 0:", len(tree_train[0]))
print("case 0:", tree_train[0][0], parent_num_train[0])

loading test set
443938194715713536
[[   0  326]
 [ 326 6281]
 [ 326 6282]
 [ 326 6283]
 [ 326 6284]
 [ 326 6285]
 [ 326 6286]
 [ 326 6287]
 [ 326 6288]
 [ 326 6289]
 [ 326 6290]
 [ 326 6291]]
774165935041093633
[[   0  327]
 [ 327 6299]
 [ 327 6300]
 [ 327 6301]
 [ 327 6302]
 [ 327 6303]
 [ 327 6304]
 [ 327 6305]
 [ 327 6306]
 [ 327 6307]
 [ 327 6308]
 [ 327 6309]
 [ 327 6310]
 [ 327 6311]
 [ 327 6312]
 [ 327 6313]
 [ 327 6314]
 [ 327 6315]
 [ 327 6316]
 [ 327 6317]]
784071228248109057
[[   0  328]
 [ 328 6039]
 [ 328 6040]
 [ 328 6041]
 [ 328 6042]
 [ 328 6043]
 [ 328 6044]
 [ 328 6045]
 [ 328 6046]
 [ 328 6047]
 [ 328 6048]
 [ 328 6049]
 [ 328 6050]
 [ 328 6051]
 [ 328 6052]
 [ 328 6053]
 [ 328 6054]
 [ 328 6055]
 [ 328 6056]
 [ 328 6057]
 [ 328 6058]
 [ 328 6059]
 [ 328 6060]
 [ 328 6061]
 [ 328 6062]
 [ 328 6063]
 [ 328 6064]
 [ 328 6065]
 [ 328 6066]
 [ 328 6067]
 [ 328 6068]
 [ 328 6069]
 [ 328 6070]
 [ 328 6071]
 [ 328 6072]
 [ 328 6073]
 [ 328 6074]
 [ 328 6075]
 [ 328 6076]
 

In [43]:
vocabulary_size = 7000
hidden_dim = 100
Nclass = 3
## 2. ini RNN model
t0 = time.time()
model = TD_RvNN.RvNN(vocabulary_size, hidden_dim, Nclass)
t1 = time.time()
print('Recursive model established,', (t1-t0)/60)

C:\Users\Admin\Documents\Uni\Last Exams To Master\Forschungspraktikum Online Polarization\Programming\polpol-rumour-sequences-RvNN-Experiments\Rumor_RvNN-master\model\TD_RvNN.py:231: UserWarning: DEPRECATION: If x is a vector, Softmax will not automatically pad x anymore in next releases. If you need it, please do it manually. The vector case is gonna be supported soon and the output will be a vector.
  return T.nnet.softmax( self.W_out.dot(final_state)+ self.b_out )


Recursive model established, 0.18199831247329712


In [46]:
Nepoch = 1
lr = 0.005
## 3. looping SGD
losses_5, losses = [], []
num_examples_seen = 0
for epoch in range(Nepoch):
    ## one SGD 
    indexs = [i for i in range(len(y_train))]
    #random.shuffle(indexs) 
    for i in indexs:
        '''print i,":", len(tree_train[i])
        print tree_train[i]
        tree_state = model._state(word_train[i], index_train[i], child_num_train[i], tree_train[i])
        print len(tree_state)
        print tree_state
        evl = model._evaluate(word_train[i], index_train[i], child_num_train[i], tree_train[i])
        print len(evl) 
        print evl'''
        loss, pred_y = model.train_step_up(word_train[i], index_train[i], parent_num_train[i], tree_train[i], y_train[i], lr)
        #print loss, pred_y
        losses.append(np.round(loss,2))
        '''if math.isnan(loss):
        #   continue 
           print loss, pred_y
           print i
           print len(tree_train[i]), len(word_train[i]), parent_num_train[i]
           print tree_train[i]
           print word_train[i]
           print 'final_state:',model._evaluate(word_train[i], index_train[i], parent_num_train[i], tree_train[i])'''
        num_examples_seen += 1
    print("epoch=%d: loss=%f" % ( epoch, np.mean(losses) ))
    #floss.write(str(time)+": epoch="+str(epoch)+" loss="+str(loss) +'\n')
    sys.stdout.flush()
    #print losses
    #exit(0)
    
    ## cal loss & evaluate
    if epoch % 5 == 0:
        losses_5.append((num_examples_seen, np.mean(losses))) 
        time = datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S')
        print("%s: Loss after num_examples_seen=%d epoch=%d: %f" % (time, num_examples_seen, epoch, np.mean(losses)))
        #floss.write(str(time)+": epoch="+str(epoch)+" loss="+str(loss) +'\n') 
        #floss.flush()       
        sys.stdout.flush()
        prediction = []
        for j in range(len(y_test)):
            #print j
            prediction.append(model.predict_up(word_test[j], index_test[j], parent_num_test[j], tree_test[j]) )   
        res = evaluation_4class(prediction, y_test) 
        print('results:', res)
        #floss.write(str(res)+'\n')
        #floss.flush() 
        sys.stdout.flush()
        ## Adjust the learning rate if loss increases
        if len(losses_5) > 1 and losses_5[-1][1] > losses_5[-2][1]:
           lr = lr * 0.5   
           print("Setting learning rate to %f" % lr)
           #floss.write("Setting learning rate to:"+str(lr)+'\n')
           #floss.flush() 
           sys.stdout.flush()
        #save_model_Recursive_gruEmb(modelPath, model)   
    #floss.flush()
    losses = []

ValueError: could not broadcast input array from shape (16,100) into shape (15,100)
Apply node that caused the error: forall_inplace,cpu,scan_fn}(Elemwise{maximum,no_inplace}.0, Subtensor{int64:int64:int32}.0, Subtensor{int64:int64:int8}.0, Subtensor{int64:int64:int8}.0, IncSubtensor{InplaceSet;:int64:}.0, IncSubtensor{InplaceSet;:int64:}.0, <TensorType(float32, matrix)>, <TensorType(float32, matrix)>, <TensorType(float32, vector)>, <TensorType(float32, matrix)>, <TensorType(float32, matrix)>, <TensorType(float32, matrix)>, <TensorType(float32, matrix)>, <TensorType(float32, vector)>, <TensorType(float32, vector)>, InplaceDimShuffle{1,0}.0)
Toposort index: 246
Inputs types: [TensorType(int64, scalar), TensorType(float32, matrix), TensorType(int32, matrix), TensorType(int32, matrix), TensorType(float32, 3D), TensorType(float32, matrix), TensorType(float32, matrix), TensorType(float32, matrix), TensorType(float32, vector), TensorType(float32, matrix), TensorType(float32, matrix), TensorT